In [46]:
import tensorflow as tf
from keras.utils import to_categorical

import keras

from tensorflow import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.wrappers.scikit_learn import KerasClassifier
from keras.models import model_from_json

In [47]:
from __future__ import division

import sys
import time
import logging

import numpy as np
from scipy.io import loadmat
from os import path
from sklearn import metrics

# change this to the path of mushu if you don't have it in your
# PYTHONPATH already
sys.path.append('../../mushu')
sys.path.append('../')

import libmushu
from libmushu.driver.replayamp import ReplayAmp
from wyrm.types import RingBuffer
import wyrm.processing as proc
from wyrm import io
from wyrm.types import Data, BlockBuffer, RingBuffer

#Classifiers
import matplotlib
import matplotlib.pyplot as plt
from sklearn.externals import joblib
from os import listdir
from os.path import isfile, join

In [48]:
logging.basicConfig(format='%(relativeCreated)10.0f %(threadName)-10s %(name)-10s %(levelname)8s %(message)s', level=logging.NOTSET)
logger = logging.getLogger(__name__)

In [49]:
# replay the experiment in real time?
REALTIME = False


TRAIN_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Train.mat'
TEST_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Test.mat'

TRAIN_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Train.mat'
TEST_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Test.mat'

CHANNEL_DATA = '../BCI_Comp_III_Wads_2004/data/eloc64.txt'

TRUE_LABELS = "WQXPLZCOMRKO97YFZDEZ1DPI9NNVGRQDJCUVRMEUOOOJD2UFYPOO6J7LDGYEGOA5VHNEHBTXOO1TDOILUEE5BFAEEXAW_K4R3MRU"

STIMULUS_CODE = {
    # cols from left to right
    1 : "agmsy5",
    2 : "bhntz6",
    3 : "ciou17",
    4 : "djpv28",
    5 : "ekqw39",
    6 : "flrx4_",
    # rows from top to bottom
    7 : "abcdef",
    8 : "ghijkl",
    9 : "mnopqr",
    10: "stuvwx",
    11: "yz1234",
    12: "56789_"
}

MARKER_DEF_TRAIN = {'target': ['target'], 'nontarget': ['nontarget']}
MARKER_DEF_TEST = {i : [i] for i in STIMULUS_CODE.values()}

SEG_IVAL = [0, 800]

In [50]:
def load_bci_TESTdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][60:,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][60:,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][60:,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[60:,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_mat.get('TargetChar')[0][60:]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [51]:
def load_bci_TRAINdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][:60,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][:60,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][:60,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[:60,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_mat.get('TargetChar')[0][:60]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [52]:
## Agregar esto en metrics.py de keras
from keras import backend as K
def precision(y_true, y_pred):
    """Precision metric.

    Only computes a batch-wise average of precision.

    Computes the precision, a metric for multi-label classification of
    how many selected items are relevant.
    """
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
    precision = true_positives / (predicted_positives + K.epsilon())
    return precision

def recall(y_true, y_pred):
    """Recall metric.

    Only computes a batch-wise average of recall.

    Computes the recall, a metric for multi-label classification of
    how many relevant items are selected.
    """
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
    recall = true_positives / (possible_positives + K.epsilon())
    return recall


def f1(y_true, y_pred):
    def recall(y_true, y_pred):
        """Recall metric.

        Only computes a batch-wise average of recall.

        Computes the recall, a metric for multi-label classification of
        how many relevant items are selected.
        """
        true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
        possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
        recall = true_positives / (possible_positives + K.epsilon())
        return recall

    def precision(y_true, y_pred):
        """Precision metric.

        Only computes a batch-wise average of precision.

        Computes the precision, a metric for multi-label classification of
        how many selected items are relevant.
        """
        true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
        predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
        precision = true_positives / (predicted_positives + K.epsilon())
        return precision
    precision = precision(y_true, y_pred)
    recall = recall(y_true, y_pred)
    return 2*((precision*recall)/(precision+recall+K.epsilon()))
    
    def f_05(y_true, y_pred):
        return((1+0.5**2)*(precision*recall)/((0.5**2)*precision+recall+K.epsilon()))


In [53]:
def train(filename):
    cnt = load_bci_TRAINdata(filename)

    fs_n = cnt.fs / 2

    b, a = proc.signal.butter(5, [10 / fs_n], btype='low')
    cnt = proc.lfilter(cnt, b, a)

#     b, a = proc.signal.butter(5, [.4 / fs_n], btype='high')
#     cnt = proc.lfilter(cnt, b, a)

    cnt = proc.subsample(cnt, 20)

    epo = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL)

    #from wyrm import plot
    #plot.plot_spatio_temporal_r2_values(proc.sort_channels(epo))
    #print JUMPING_MEANS_IVALS
    #plot.plt.show()

    fv = proc.create_feature_vectors(epo)
#     X = fv.data
#     y = fv.axes[0]
    clf = train_MLP(fv)

    return clf

In [54]:
def online_experiment(amp, cfy, subject):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    
    file = open('sim_training_MLP'+subject+'.txt', 'w')
    file.write('MLP Online simulation'+subject)
    
    # csv results file
    filename = 'results/'+subject+'/Results_MLP_'+subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,precision_acum,f1_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames)

    chfilename = 'results/'+subject+'/CharacterResults_MLP_'+subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames) 


    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [10 / fn], btype='low')
#     b_high, a_high = proc.signal.butter(5, [.4 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
#     zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
        ## enter the block buffer
        #buf.append(cnt)
        #cnt = buf.get()
        #if not cnt:
        #    continue

        # low-pass and subsample
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
#         cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        cnt = proc.subsample(cnt, 20)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, SEG_IVAL, newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL, newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = proc.create_feature_vectors(epo)
        fv_train = proc.create_feature_vectors(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)
        
        
        cfy_out = cfy.predict(fv.data)[:,1]
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict_classes(fv.data) 
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, cfy_out)
        
        report = metrics.classification_report(y_true, y_pred)
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)
        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
          
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, n_trial))
                    correct_letter = True
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                            current_letter, int(markers_processed/12)))


                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, f1, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(f1)+','+str(accuracy))

                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)
    
                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))
            

            markers_processed += 1

                
#             if (markers_processed%12 == 0) & (markers_processed != 180) & (not correct_letter):
#                 current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
#                 if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                     file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                   current_letter, int(markers_processed/12)))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
#                     correct_letter = True
           
#             elif markers_processed == 180: # 12 trials x 15 repetitions = 180
#                 endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
#                 # Set all probabilities to zero
#                 letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
#                 markers_processed = 0
#                 if not correct_letter:
#                     file.write('\n\nFailed to predict character #{} in 15 trials'.format(len(endresult)))
#                     file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
                    
#                 correct_letter = False
# #                 current_letter_idx += 1
# #                 print('letter idx', current_letter_idx)
# #                 current_letter = TRUE_LABELS[current_letter_idx].lower()
#             markers_processed += 1
#         print(letter_prob)
#         logger.debug("".join([i[0] for i in sorted(letter_prob.items(), key=lambda x: x[1], reverse=True)]).replace(current_letter, " %s " % current_letter))

        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()

    amp.stop()


In [55]:


from __future__ import division

import time

import numpy as np

from libmushu.amplifier import Amplifier


class RReeplayAmp(Amplifier):

    def configure(self, data, marker, channels, fs, realtime=True, blocksize_ms=None, blocksize_samples=None):
        """

        Parameters
        ----------
        data
        marker
        channels
        fs
        realtime
        blocksize_ms : float
            blocksize in milliseconds
        blocksize_samples : int
            blocksize in samples

        Raises
        ------
        TypeError :
            if ``blocksize_ms`` and ``blocksize_s`` are given.

        """
        if [blocksize_ms, blocksize_samples].count(None) != 1:
            raise TypeError("blocksize_ms and blocksize_samples are mutually exclusive.")

        self.data = data
        # slow python
        self.marker = marker
        # fast numpy
        self.marker_ts = np.array([ts for ts, s in marker])
        self.marker_s = np.array([s for ts, s in marker])
        self.channels = channels
        self.fs = fs
        self.realtime = realtime

        if blocksize_ms:
            samples = fs * (blocksize_ms / 1000)
            if not samples.is_integer():
                raise ValueError("Resulting blocksize is not integer, please fix the blocksize_ms.")
            self.samples = samples
        if blocksize_samples:
            self.samples = blocksize_samples

    def start(self):
        self.last_sample_time = time.time()
        self.pos = 0

    def stop(self):
        pass

    def get_data(self):
        """

        Returns
        -------
        chunk, markers: Markers is time in ms since relative to the
        first sample of that block.

        """
        if self.realtime:
            elapsed = time.time() - self.last_sample_time
            blocks = (self.fs * elapsed) // self.samples
            samples = int(blocks * self.samples)
            
        else:
            samples = self.samples
      
        elapsed = samples / self.fs
        self.last_sample_time += elapsed
        # data
        chunk = self.data[self.pos:int(self.pos+samples)]
        #self.data = self.data[samples:]
        # markers

        # slow python version
        #markers = [x for x in self.marker if x[0] < elapsed * 1000]
        #self.marker = [x for x in self.marker if x[0] >= elapsed * 1000]
        #self.marker = [[x[0] - elapsed * 1000, x[1]] for x in self.marker]

        # fast numpy version
        mask = self.marker_ts < (elapsed * 1000) 
        markers = list(zip(self.marker_ts[mask], self.marker_s[mask]))
        self.marker_ts = self.marker_ts[~mask]
        self.marker_s = self.marker_s[~mask]
        self.marker_ts -= elapsed * 1000

        self.pos += samples
        return chunk, markers

    def get_channels(self):
        return self.channels

    def get_sampling_frequency(self):
        return self.fs

    @staticmethod
    def is_available():
        return True


# 1. Model Construction

In [56]:
def train_MLP(fv):
    X_train = fv.data
    y_train = fv.axes[0]
    #Creating the architecture (layers)
    n_features = X_train.shape[1]
    n_channels = 64
    model = Sequential()
    model.add(Dense(300, input_dim = n_features, activation = 'tanh'))
    model.add(Dropout(0.5))
    model.add(Dense(150, activation = 'tanh'))
    model.add(Dropout(0.5))
    model.add(Dense(2, activation = 'softmax'))

    #Compiling the model
    model.compile(optimizer='sgd',
                  loss='binary_crossentropy',       
                  metrics=['accuracy', precision, recall, f1], weighted_metrics = [f1]) 

    #Train the model
    n_P300 = X_train[y_train == 1].shape[0]
    n_nonP300 = X_train[y_train == 0].shape[0]
    H = model.fit(X_train, to_categorical(y_train), epochs = 100, validation_split = 0.2, 
                  class_weight = {1: n_nonP300/n_P300*0.4, 0: n_P300/n_nonP300})
    return model

In [22]:
subject = 'B'
if subject == 'A':
    TRAIN_DATA = TRAIN_DATA_A
elif subject == 'B':
    TRAIN_DATA = TRAIN_DATA_B
data_m = loadmat(TRAIN_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars

In [55]:
clf = train(TRAIN_DATA)

Train on 8640 samples, validate on 2160 samples
Epoch 1/100
8640/8640 [==============================] - 6s 716us/step - loss: 0.4303 - acc: 0.4238 - precision: 0.4238 - recall: 0.4238 - f1: 0.4238 - weighted_f1: 0.2133 - val_loss: 0.3317 - val_acc: 0.3153 - val_precision: 0.3153 - val_recall: 0.3153 - val_f1: 0.3153 - val_weighted_f1: 0.1584
Epoch 2/100
8640/8640 [==============================] - 4s 496us/step - loss: 0.3551 - acc: 0.3907 - precision: 0.3907 - recall: 0.3907 - f1: 0.3907 - weighted_f1: 0.1991 - val_loss: 0.3188 - val_acc: 0.3134 - val_precision: 0.3134 - val_recall: 0.3134 - val_f1: 0.3134 - val_weighted_f1: 0.1577
Epoch 3/100
8640/8640 [==============================] - 4s 512us/step - loss: 0.3315 - acc: 0.3853 - precision: 0.3853 - recall: 0.3853 - f1: 0.3853 - weighted_f1: 0.1978 - val_loss: 0.3145 - val_acc: 0.2657 - val_precision: 0.2657 - val_recall: 0.2657 - val_f1: 0.2657 - val_weighted_f1: 0.1341
Epoch 4/100
8640/8640 [==============================] - 4s 4

8640/8640 [==============================] - 5s 533us/step - loss: 0.1937 - acc: 0.7094 - precision: 0.7094 - recall: 0.7094 - f1: 0.7094 - weighted_f1: 0.3568 - val_loss: 0.3959 - val_acc: 0.6611 - val_precision: 0.6611 - val_recall: 0.6611 - val_f1: 0.6611 - val_weighted_f1: 0.3301
Epoch 63/100
8640/8640 [==============================] - 5s 549us/step - loss: 0.1940 - acc: 0.7139 - precision: 0.7139 - recall: 0.7139 - f1: 0.7139 - weighted_f1: 0.3591 - val_loss: 0.3854 - val_acc: 0.6542 - val_precision: 0.6542 - val_recall: 0.6542 - val_f1: 0.6542 - val_weighted_f1: 0.3266
Epoch 64/100
8640/8640 [==============================] - 5s 575us/step - loss: 0.1939 - acc: 0.7189 - precision: 0.7189 - recall: 0.7189 - f1: 0.7189 - weighted_f1: 0.3611 - val_loss: 0.3746 - val_acc: 0.6444 - val_precision: 0.6444 - val_recall: 0.6444 - val_f1: 0.6444 - val_weighted_f1: 0.3219
Epoch 65/100
8640/8640 [==============================] - 5s 525us/step - loss: 0.1860 - acc: 0.7247 - precision: 0.724

In [23]:
filename = 'Trained Classifiers/'+subject+'/MLP_'+subject+'.json'
weights_filename = 'Trained Classifiers/'+subject+'/MLP_weights_'+subject+'.h5'

In [56]:
# serialize model to JSON
model_json = clf.to_json()
with open(filename, "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
clf.save_weights(weights_filename)
print("Saved model to disk")


Saved model to disk


In [24]:
# load json and create model
json_file = open(filename, 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights(weights_filename)
print("Loaded model from disk")
# evaluate loaded model on test data
loaded_model.compile(optimizer='sgd',
                  loss='binary_crossentropy',       
                  metrics=['accuracy', precision, recall, f1], weighted_metrics = [f1]) 
clf = loaded_model

Loaded model from disk


# 2. Simulation

In [25]:
bbuffer = BlockBuffer(12)
cnt = load_bci_TESTdata(TRAIN_DATA)

In [26]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [27]:

online_experiment(amp, clf, subject)


DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__

Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 150.6202220916748
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 17.95172691345215
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.3333333333333333
time 15.958786010742188
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.25
time 15.956878662109375
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.2
time 23.935556411743164
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.16666666666666666
time 17.95220375061035


DEBUG:__main__:Markers processed: 
DEBUG:__main__:7
DEBUG:__main__:Markers processed: 
DEBUG:__main__:8
DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.14285714285714285
time 18.941640853881836
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.125
time 18.949508666992188
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.1111111111111111
time 17.953157424926758
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.125 	f1:  0.2 	accuracy:  0.2
time 21.93903923034668


DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 

...

Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.7022160664819944 	precision:  0.26489028213166144 	f1:  0.3846737481031866 	accuracy:  0.6260087618169241
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 61.89584732055664
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.7022160664819944 	precision:  0.26475195822454306 	f1:  0.38452787258248 	accuracy:  0.6258644536652835
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 38.88988494873047
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7022160664819944 	precision:  0.26475195822454306 	f1:  0.38452787258248 	accuracy:  0.6259506798801567
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 26.927947998046875
Predicho:  [1] 	Verdadero:  [1] [ True]


DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eoidwueuewwfoaahxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eoidwueuewwfoaahxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO



P300 classification metrics...
recall:  0.7026279391424619 	precision:  0.2651356993736952 	f1:  0.3849943160287988 	accuracy:  0.626036866359447
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 41.40329360961914
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.7026279391424619 	precision:  0.2649973917579551 	f1:  0.3848484848484848 	accuracy:  0.6258926514627966
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 68.3441162109375
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7026279391424619 	precision:  0.2649973917579551 	f1:  0.3848484848484848 	accuracy:  0.6259788116075541


DEBUG:__main__:eoidwueuewwfoaahxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eoidwueuewwfoaahxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eoidwueuewwfoaahxtqttzum


Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 80.29913902282715
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7026279391424619 	precision:  0.2649973917579551 	f1:  0.3848484848484848 	accuracy:  0.6260649320746028
Character prediction metrics...
Current accuracy: 78.26086956521739
23/25 characters predicted
time 33.908843994140625
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.7030386740331491 	precision:  0.2653806047966632 	f1:  0.3853141559424679 	accuracy:  0.6261510128913443
Character prediction metrics...
Current accuracy: 79.16666666666666
24/25 characters predicted
Accuracy: 79.16666666666666


# INTERSUJETO

In [34]:
def online_experiment_intersujeto(amp, cfy, inter_subject):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    
    file = open('sim_training_MLP'+inter_subject+'.txt', 'w')
    file.write('MLP Online simulation '+inter_subject)
    
    # csv results file
    filename = 'results/Intersujeto/'+inter_subject+'/Results_MLP_'+inter_subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,precision_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames)

    chfilename = 'results/Intersujeto/'+inter_subject+'/CharacterResults_MLP_'+inter_subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames) 
    

    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [10 / fn], btype='low')
#     b_high, a_high = proc.signal.butter(5, [.4 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
#     zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
        ## enter the block buffer
        #buf.append(cnt)
        #cnt = buf.get()
        #if not cnt:
        #    continue

        # low-pass and subsample
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
#         cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        cnt = proc.subsample(cnt, 20)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, SEG_IVAL, newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL, newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = proc.create_feature_vectors(epo)
        fv_train = proc.create_feature_vectors(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)

        cfy_out = cfy.predict(fv.data)[:,1]
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict_classes(fv.data) 
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, cfy_out)
        
        report = metrics.classification_report(y_true, y_pred)
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)        

        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
               
              
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, n_trial))
                    correct_letter = True
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                           current_letter, int(markers_processed/12)))

                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(accuracy))

                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)
                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))
        

            markers_processed += 1

                
#             if (markers_processed%12 == 0) & (markers_processed != 180) & (not correct_letter):
#                 current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
#                 if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                     file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                   current_letter, int(markers_processed/12)))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
#                     correct_letter = True
           
#             elif markers_processed == 180: # 12 trials x 15 repetitions = 180
#                 endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
#                 # Set all probabilities to zero
#                 letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
#                 markers_processed = 0
#                 if not correct_letter:
#                     file.write('\n\nFailed to predict character #{} in 15 trials'.format(len(endresult)))
#                     file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
                    
#                 correct_letter = False
# #                 current_letter_idx += 1
# #                 print('letter idx', current_letter_idx)
# #                 current_letter = TRUE_LABELS[current_letter_idx].lower()
#             markers_processed += 1
#         print(letter_prob)
#         logger.debug("".join([i[0] for i in sorted(letter_prob.items(), key=lambda x: x[1], reverse=True)]).replace(current_letter, " %s " % current_letter))

        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()
    resultsFile.close()

    amp.stop()


In [70]:
inter_subject = 'A-clfB'
if inter_subject == 'A-clfB':
    TEST_DATA = TRAIN_DATA_A
    subject = 'B'
elif inter_subject == 'B-clfA':
    TEST_DATA = TRAIN_DATA_B  
    subject = 'A'
data_m = loadmat(TEST_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars
TRUE_LABELS

'W_EKTLBWXEPOUIKZERYOOTHQI'

## 1. Training (off-line)

In [71]:
filename = 'Trained Classifiers/'+subject+'/MLP_'+subject+'.json'
weights_filename = 'Trained Classifiers/'+subject+'/MLP_weights_'+subject+'.h5'

In [72]:
# load json and create model
json_file = open(filename, 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights(weights_filename)
print("Loaded model from disk")
# evaluate loaded model on test data
loaded_model.compile(optimizer='sgd',
                  loss='binary_crossentropy',       
                  metrics=['accuracy', precision, recall, f1], weighted_metrics = [f1]) 
clf = loaded_model

Loaded model from disk


## 2. Online experiment

In [73]:
bbuffer = BlockBuffer(12)
cnt = load_bci_TESTdata(TEST_DATA)

In [74]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [75]:
online_experiment_intersujeto(amp, clf, inter_subject)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true samples.
  'recall', 'true', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 
DEBUG:__main__:5
DEBUG:__main__:Markers proc

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 210.4346752166748
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 14.960527420043945
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.3333333333333333
time 15.957117080688477
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 13.961315155029297
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.4
time 14.961004257202148
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 11.968851089477539
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
re

DEBUG:__main__:Markers processed: 
DEBUG:__main__:8
DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13



P300 classification metrics...
recall:  0.5 	precision:  0.3333333333333333 	f1:  0.4 	accuracy:  0.625
time 17.943143844604492
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5 	precision:  0.25 	f1:  0.3333333333333333 	accuracy:  0.5555555555555556
time 13.96322250366211
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.25 	f1:  0.3333333333333333 	accuracy:  0.6
time 13.962268829345703
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5 	precision:  0.2 	f1:  0.28571428571428575 	accuracy:  0.5454545454545454
time 15.95759391784668
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.2 	f1:  0.28571428571428575 	accuracy:  0.5833333333333334
time 18.949508666992188
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  0.3333333333333333 	f1:  0.4444444444444444

DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18
DEBUG:__main__:Markers processed: 


...

Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.4889196675900277 	precision:  0.20159908623643633 	f1:  0.2854832187626365 	accuracy:  0.5922934933087217
Character prediction metrics...
Current accuracy: 21.73913043478261
23/25 characters predicted
time 24.934053421020508
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.4889196675900277 	precision:  0.20159908623643633 	f1:  0.2854832187626365 	accuracy:  0.5923875432525951
Character prediction metrics...
Current accuracy: 21.73913043478261
23/25 characters predicted
time 19.946813583374023
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.4889196675900277 	precision:  0.20159908623643633 	f1:  0.2854832187626365 	accuracy:  0.5924815498154982
Character prediction metrics...
Current accuracy: 21.73913043478261
23/25 characters predicted
time 20.944595336914062
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
reca

DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:94mkviwwtkjqshtzotpostm
DEBUG:__main__:Markers processed: 
DEBUG:__main__:176
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:94mkviwwtkjqshtzotpostm
DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:94mkviwwtkjqshtzotpostm
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:94mkviwwtkjqshtzotpostm
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:94mkviwwtkjqshtzotpostm
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI


 [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.48756906077348067 	precision:  0.2014840182648402 	f1:  0.2851373182552504 	accuracy:  0.5920719059691173
Character prediction metrics...
Current accuracy: 21.73913043478261
23/25 characters predicted
time 22.94325828552246
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.48756906077348067 	precision:  0.2013690815744438 	f1:  0.2850222042793702 	accuracy:  0.5919354838709677
Character prediction metrics...
Current accuracy: 21.73913043478261
23/25 characters predicted
time 20.945072174072266
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.48756906077348067 	precision:  0.20125427594070697 	f1:  0.284907183212268 	accuracy:  0.5917991246256623
Character prediction metrics...
Current accuracy: 21.73913043478261
23/25 characters predicted
time 21.9423770904541
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.487569

DEBUG:__main__:94mkviwwtkjqshtzotpostmz


Character prediction metrics...
Current accuracy: 20.833333333333336
24/25 characters predicted
Accuracy: 20.833333333333336


## Sujeto C

In [57]:
def load_bci_TRAINdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[:30,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [58]:
def load_bci_TESTdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[30:,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [59]:
labels = 'CATDOGFISHWATERBOWLHATHATGLOVESHOESFISHRAT'
path_ = '../BCI_Comp_II_2003/data/'
datafiles = [join(path_,f) for f in listdir(path_) if isfile(join(path_, f))]
training_set = [f for i,f in enumerate(datafiles) if '12' not in f and 'eloc64' not in f]
testing_set = [f for i,f in enumerate(datafiles) if '12' in f and 'eloc64' not in f]

In [61]:
# load the training set
dat_train = load_bci_TRAINdata2(training_set)


In [62]:
TRUE_LABELS = labels[30:]
TRUE_LABELS

'SHOESFISHRAT'

### Training

In [63]:
def train_d2(dat):
    cnt = dat

    fs_n = cnt.fs / 2

    b, a = proc.signal.butter(5, [10 / fs_n], btype='low')
    cnt = proc.lfilter(cnt, b, a)

#     b, a = proc.signal.butter(5, [.4 / fs_n], btype='high')
#     cnt = proc.lfilter(cnt, b, a)

    cnt = proc.subsample(cnt, 20)

    epo = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL)

    #from wyrm import plot
    #plot.plot_spatio_temporal_r2_values(proc.sort_channels(epo))
    #print JUMPING_MEANS_IVALS
    #plot.plt.show()

    fv = proc.create_feature_vectors(epo)
    clf = train_MLP(fv)

    return clf

In [64]:
clf = train_d2(dat_train)

Train on 4348 samples, validate on 1088 samples
Epoch 1/100
4348/4348 [==============================] - 1s 324us/step - loss: 0.4404 - acc: 0.4637 - precision: 0.4637 - recall: 0.4637 - f1: 0.4637 - weighted_f1: 0.2335 - val_loss: 0.3271 - val_acc: 0.3732 - val_precision: 0.3732 - val_recall: 0.3732 - val_f1: 0.3732 - val_weighted_f1: 0.1875
Epoch 2/100
4348/4348 [==============================] - 1s 218us/step - loss: 0.3791 - acc: 0.4602 - precision: 0.4602 - recall: 0.4602 - f1: 0.4602 - weighted_f1: 0.2333 - val_loss: 0.3144 - val_acc: 0.4283 - val_precision: 0.4283 - val_recall: 0.4283 - val_f1: 0.4283 - val_weighted_f1: 0.2152
Epoch 3/100
4348/4348 [==============================] - 1s 261us/step - loss: 0.3568 - acc: 0.4492 - precision: 0.4492 - recall: 0.4492 - f1: 0.4492 - weighted_f1: 0.2277 - val_loss: 0.3022 - val_acc: 0.3465 - val_precision: 0.3465 - val_recall: 0.3465 - val_f1: 0.3465 - val_weighted_f1: 0.1746
Epoch 4/100
4348/4348 [==============================] - 1s 2

4348/4348 [==============================] - 1s 271us/step - loss: 0.2905 - acc: 0.4105 - precision: 0.4105 - recall: 0.4105 - f1: 0.4105 - weighted_f1: 0.2101 - val_loss: 0.2880 - val_acc: 0.3925 - val_precision: 0.3925 - val_recall: 0.3925 - val_f1: 0.3925 - val_weighted_f1: 0.1977
Epoch 29/100
4348/4348 [==============================] - 1s 260us/step - loss: 0.2868 - acc: 0.4340 - precision: 0.4340 - recall: 0.4340 - f1: 0.4340 - weighted_f1: 0.2222 - val_loss: 0.2862 - val_acc: 0.3989 - val_precision: 0.3989 - val_recall: 0.3989 - val_f1: 0.3989 - val_weighted_f1: 0.2011
Epoch 30/100
4348/4348 [==============================] - 1s 264us/step - loss: 0.2890 - acc: 0.4161 - precision: 0.4161 - recall: 0.4161 - f1: 0.4161 - weighted_f1: 0.2108 - val_loss: 0.2875 - val_acc: 0.3989 - val_precision: 0.3989 - val_recall: 0.3989 - val_f1: 0.3989 - val_weighted_f1: 0.2008
Epoch 31/100
4348/4348 [==============================] - 1s 266us/step - loss: 0.2893 - acc: 0.4296 - precision: 0.429

4348/4348 [==============================] - 1s 262us/step - loss: 0.2830 - acc: 0.4561 - precision: 0.4561 - recall: 0.4561 - f1: 0.4561 - weighted_f1: 0.2312 - val_loss: 0.2806 - val_acc: 0.4669 - val_precision: 0.4669 - val_recall: 0.4669 - val_f1: 0.4669 - val_weighted_f1: 0.2344
Epoch 56/100
4348/4348 [==============================] - 1s 261us/step - loss: 0.2797 - acc: 0.4588 - precision: 0.4588 - recall: 0.4588 - f1: 0.4588 - weighted_f1: 0.2341 - val_loss: 0.2799 - val_acc: 0.4706 - val_precision: 0.4706 - val_recall: 0.4706 - val_f1: 0.4706 - val_weighted_f1: 0.2361
Epoch 57/100
4348/4348 [==============================] - 1s 258us/step - loss: 0.2820 - acc: 0.4646 - precision: 0.4646 - recall: 0.4646 - f1: 0.4646 - weighted_f1: 0.2355 - val_loss: 0.2817 - val_acc: 0.5083 - val_precision: 0.5083 - val_recall: 0.5083 - val_f1: 0.5083 - val_weighted_f1: 0.2551
Epoch 58/100
4348/4348 [==============================] - 1s 259us/step - loss: 0.2804 - acc: 0.4627 - precision: 0.462

4348/4348 [==============================] - 1s 266us/step - loss: 0.2744 - acc: 0.4692 - precision: 0.4692 - recall: 0.4692 - f1: 0.4692 - weighted_f1: 0.2395 - val_loss: 0.2738 - val_acc: 0.4862 - val_precision: 0.4862 - val_recall: 0.4862 - val_f1: 0.4862 - val_weighted_f1: 0.2436
Epoch 83/100
4348/4348 [==============================] - 1s 311us/step - loss: 0.2790 - acc: 0.4742 - precision: 0.4742 - recall: 0.4742 - f1: 0.4742 - weighted_f1: 0.2399 - val_loss: 0.2738 - val_acc: 0.4651 - val_precision: 0.4651 - val_recall: 0.4651 - val_f1: 0.4651 - val_weighted_f1: 0.2334
Epoch 84/100
4348/4348 [==============================] - 1s 289us/step - loss: 0.2703 - acc: 0.4823 - precision: 0.4823 - recall: 0.4823 - f1: 0.4823 - weighted_f1: 0.2452 - val_loss: 0.2746 - val_acc: 0.5211 - val_precision: 0.5211 - val_recall: 0.5211 - val_f1: 0.5211 - val_weighted_f1: 0.2612
Epoch 85/100
4348/4348 [==============================] - 1s 315us/step - loss: 0.2800 - acc: 0.4834 - precision: 0.483

In [65]:
subject = 'C'
filename = 'Trained Classifiers/'+subject+'/MLP_'+subject+'.json'
weights_filename = 'Trained Classifiers/'+subject+'/MLP_weights_'+subject+'.h5'

In [66]:
# serialize model to JSON
model_json = clf.to_json()
with open(filename, "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
clf.save_weights(weights_filename)
print("Saved model to disk")


Saved model to disk


In [24]:
# load json and create model
json_file = open(filename, 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights(weights_filename)
print("Loaded model from disk")
# evaluate loaded model on test data
loaded_model.compile(optimizer='sgd',
                  loss='binary_crossentropy',       
                  metrics=['accuracy', precision, recall, f1], weighted_metrics = [f1]) 
clf = loaded_model

Loaded model from disk


### Online experiment

In [67]:
bbuffer = BlockBuffer(12)
dat_test = load_bci_TESTdata2(training_set)
cnt = dat_test

In [68]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [69]:
online_experiment(amp, clf, subject)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 
DEBUG:__main__:5
DEBUG:__main__:Markers processed: 
DEBUG:__main__:6
DEBUG:__main__:Markers processed: 
DEBUG:__main__:7
DEBUG:__main__:Markers processed: 
DEBUG:__main__:8
DEBUG:__main__:Markers processed: 
DEBUG:__main__:9


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 69.81253623962402
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 10.96963882446289
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  1.0 	precision:  1.0 	f1:  1.0 	accuracy:  1.0
time 9.971857070922852
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.75
time 10.969877243041992
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.8
time 12.964963912963867
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.8333333333333334
time 11.968135833740234
Predicho:  [1] 	Verdadero:  [1

DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 

Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.6 	f1:  0.7499999999999999 	accuracy:  0.8181818181818182
time 21.93903923034668
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.6 	f1:  0.7499999999999999 	accuracy:  0.8333333333333334
time 12.965917587280273
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.7692307692307693
time 10.969877243041992
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.7857142857142857
time 13.963460922241211
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:  0.6666666666666666 	accuracy:  0.8
time 12.970924377441406
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.5 	f1:


DEBUG:__main__:18
DEBUG:__main__:Markers processed: 
DEBUG:__main__:19
DEBUG:__main__:Markers processed: 
DEBUG:__main__:20
DEBUG:__main__:Markers processed: 
DEBUG:__main__:21
DEBUG:__main__:Markers processed: 
DEBUG:__main__:22
DEBUG:__main__:Markers processed: 
DEBUG:__main__:23


...

Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.2390745501285347 	f1:  0.3722481654436291 	accuracy:  0.5249873801110551
Character prediction metrics...
Current accuracy: 40.0
10/12 characters predicted
time 19.946575164794922
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.2390745501285347 	f1:  0.3722481654436291 	accuracy:  0.5252270433905146
Character prediction metrics...
Current accuracy: 40.0
10/12 characters predicted
time 23.937225341796875
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.2390745501285347 	f1:  0.3722481654436291 	accuracy:  0.5254664649520928
Character prediction metrics...
Current accuracy: 40.0
10/12 characters predicted
time 21.942138671875
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.238869

DEBUG:__main__:175
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shpe5ecsnl
DEBUG:__main__:Markers processed: 
DEBUG:__main__:176
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shpe5ecsnl
DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shpe5ecsnl
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shpe5ecsnl


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.2386655260906758 	f1:  0.37175216522318455 	accuracy:  0.5251762336354482
Character prediction metrics...
Current accuracy: 40.0
10/12 characters predicted
time 24.934768676757812
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.23846153846153847 	f1:  0.37150466045272973 	accuracy:  0.5249119275289381
Character prediction metrics...
Current accuracy: 40.0
10/12 characters predicted
time 20.943641662597656
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.23825789923142612 	f1:  0.3712574850299401 	accuracy:  0.5246478873239436
Character prediction metrics...
Current accuracy: 40.0
10/12 characters predicted
time 20.946264266967773
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0

DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shpe5ecsnl
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shpe5ecsnly


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.2380546075085324 	f1:  0.37101063829787234 	accuracy:  0.5246231155778894
Character prediction metrics...
Current accuracy: 40.0
10/12 characters predicted
time 20.94411849975586
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.8403614457831325 	precision:  0.2380546075085324 	f1:  0.37101063829787234 	accuracy:  0.5248618784530387
Character prediction metrics...
Current accuracy: 36.36363636363637
11/12 characters predicted
Accuracy: 36.36363636363637
